# Optimize Initial Conditions
## Brute Force

In [1]:
from scipy.optimize import brute,optimize
import numpy as np
from datetime import datetime,timedelta
import pandas as pd
import ray

In [2]:
LoadBH=True
if LoadBH:
    import LearnerICRayNoLoadBH as L
else:
    import LearnerICRayNoLoad as L

In [3]:
def load_confirmed(state, start_date):
    dateparse = lambda x: datetime.strptime(x, '%Y-%m-%d')
    df = pd.read_csv('./data/confirmados.csv',delimiter=',',parse_dates=True, date_parser=dateparse)
    y=[]
    x=[]
    for i in range(0,len(df.date)):
        y.append(df[state].values[i])
        x.append(df.date.values[i])
    df2=pd.DataFrame(data=y,index=x,columns=[""])
    df2=df2[start_date:]
    del x,y,df,dateparse
    return df2

def load_dead(state, start_date):
    dateparse = lambda x: datetime.strptime(x, '%Y-%m-%d')
    df = pd.read_csv('./data/mortes.csv',delimiter=',',parse_dates=True, date_parser=dateparse)
    y=[]
    x=[]
    for i in range(0,len(df.date)):
        y.append(df[state].values[i])
        x.append(df.date.values[i])
    df2=pd.DataFrame(data=y,index=x,columns=[""])
    df2=df2[start_date:]
    del x,y,df,dateparse
    return df2

In [4]:
# Initial parameters
dfparam = pd.read_csv("data/param.csv")
dfparam

state  start-date  prediction-range         s0  e0  a0   i0   r0   d0  \
0    SP  2020-03-15               200  8000000.0   0   0  800  300  250   
1    ES  2020-04-01               200   475000.0   0   0   50  250   50   
2    MG  2020-04-01               200  1100000.0   0   0  200  250   40   
3    RJ  2020-03-20               200   700000.0   0   0  800  250   50   
4    CE  2020-03-20               200   800000.0   0   0  800  250   50   
5    PE  2020-03-20               200   700000.0   0   0  800  250  100   
6    AM  2020-03-20               200   700000.0   0   0  800  250  100   

   START  RATIO  WCASES  WREC  
0    100   0.15    0.55  0.01  
1    100   0.15    0.65  0.01  
2    100   0.15    0.55  0.01  
3    100   0.15    0.50  0.01  
4    100   0.15    0.50  0.01  
5    100   0.15    0.50  0.01  
6    100   0.15    0.50  0.01

In [5]:
df = pd.read_csv("data/dados_total_estados.csv")
df

index        date state   city place_type  confirmed  deaths  \
0          0  2020-06-06    SE  TOTAL      state       8972     208   
1          1  2020-06-05    SE  TOTAL      state       8577     198   
2          2  2020-06-04    SE  TOTAL      state       8200     186   
3          3  2020-06-03    SE  TOTAL      state       7989     180   
4          4  2020-06-02    SE  TOTAL      state       7555     172   
...      ...         ...   ...    ...        ...        ...     ...   
2244  158210  2020-03-11    BA  TOTAL      state          3       0   
2245  158211  2020-03-10    BA  TOTAL      state          2       0   
2246  158212  2020-03-09    BA  TOTAL      state          2       0   
2247  158213  2020-03-07    BA  TOTAL      state          2       0   
2248  158214  2020-03-06    BA  TOTAL      state          1       0   

      order_for_place  is_last      popEst  city_ibge_code  \
0                  74     True   2298696.0            28.0   
1                  73    False   2298696.0            28.0   
2                  72    False   2298696.0            28.0   
3                  71    False   2298696.0            28.0   
4                  70    False   2298696.0            28.0   
...               ...      ...         ...             ...   
2244                5    False  14873064.0            29.0   
2245                4    False  14873064.0            29.0   
2246                3    False  14873064.0            29.0   
2247                2    False  14873064.0            29.0   
2248                1    False  14873064.0            29.0   

      confirmed_per_100k_inhabitants  death_rate  
0                          390.30824      0.0232  
1                          373.12459      0.0231  
2                          356.72399      0.0227  
3                          347.54487      0.0225  
4                          328.66460      0.0228  
...                              ...         ...  
2244                         0.02017      0.0000  
2245                         0.01345      0.0000  
2246                         0.01345      0.0000  
2247                         0.01345      0.0000  
2248                         0.00672      0.0000  

[2249 rows x 13 columns]

In [6]:
@ray.remote(memory=50 * 1024 * 1024, max_calls=2)
def opt(state,s0,i0,e0,a0,r0,d0,date,startNCases, ratio, predict_range, version):
    optimal = brute(fobjective,        
        ranges=[slice(0.8*s0,1.2*s0,0.4/3*s0),slice(-4,4,2),slice(0.8*i0,1.2*i0,0.1*i0),\
                slice(0.3,0.6,0.1),slice(0.1,0.15,0.05)],
        args=(state,e0,a0,r0,d0,date,startNCases, ratio, predict_range, version), \
        full_output=True, disp=True, finish=optimize.fmin)
    return optimal[0]

In [7]:
from scipy.integrate import odeint
import os
import sys
import io
import gc

def append_new_line(file_name, text_to_append):
    #Append given text as a new line at the end of file
    # Open the file in append & read mode ('a+')
    with open(file_name, "a+") as file_object:
        # Move read cursor to the start of file.
        file_object.seek(0)
        # If file is not empty then append '\n'
        data = file_object.read(9999999)
        if len(data) > 0:
            file_object.write("\n")
        # Append text at the end of file
        file_object.write(text_to_append)

def fobjective(point,state,e0,a0,r0,d0,date,startNCases, ratio, predict_range, version):
    
    dead =  load_dead(state,date)
    data = load_confirmed(state,date)*(1-ratio)-dead

    cleanRecovered=False
    s0, deltaDate, i0, weigthCases, weigthRecov = point
    end_date=datetime.strptime(date, "%Y-%m-%d") + timedelta(days=+int(deltaDate))

    f=L.Learner.remote(state, end_date.strftime("%Y-%m-%d"), predict_range,\
                       s0, e0, a0, i0, r0, d0, startNCases, ratio, weigthCases, weigthRecov, \
                       cleanRecovered, version, data, dead, savedata=False)
    result = f.train.remote() 
    result = ray.get(result) 

    del end_date,cleanRecovered, data, dead, point         

    gc.collect()

    return result

In [8]:
states=['SP','ES','MG','RJ','PE','CE','AM']
allStates=True
version="10"
ray.shutdown()
GB=1024*1024*1024
MB=1024*1024
import cupy
import torch
ray.init(object_store_memory=500*MB,memory=1*GB,lru_evict=True,\
         driver_object_store_memory=50*MB,num_gpus=12,num_cpus=7)
gc.enable()

runID=[]
if allStates:
    for state in states:
        strFile='./results/history_'+state+version+'.csv'
        if os.path.isfile(strFile):
            os.remove(strFile)
        query = dfparam.query('state == "{}"'.format(state)).reset_index()
        parameters = np.array(query.iloc[:, 2:])[0]
        startdate,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec = parameters
        runID.append(opt.remote(state,s0,i0,e0,a0,r0,d0,startdate,startNCases, \
                                                    ratio, predict_range, version))
else:
    state = "ES" 
    #remove previous history file
    strFile='./results/history_'+state+version+'.csv'
    if os.path.isfile(strFile):
        os.remove(strFile)
    query = dfparam.query('state == "{}"'.format(state)).reset_index()
    parameters = np.array(query.iloc[:, 2:])[0]
    startdate,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec = parameters
    runID.append(opt.remote(state,s0,i0,e0,a0,r0,d0,startdate,startNCases, \
                                                    ratio, predict_range, version))

2020-06-15 18:07:14,728	INFO resource_spec.py:212 -- Starting Ray with 0.98 GiB memory available for workers and up to 0.49 GiB for objects. You can adjust these settings with ray.init(memory=<bytes>, object_store_memory=<bytes>).
2020-06-15 18:07:15,108	INFO services.py:1170 -- View the Ray dashboard at localhost:8266


In [ ]:
optimal=ray.get(runID)

(pid=145312) basinhopping step 0: f 1.12102e+08
(pid=145407) basinhopping step 0: f 6.2945e+07
(pid=145328) basinhopping step 0: f -1.62778e+13
(pid=145328) basinhopping step 1: f -1.62778e+13 trial_f 2.62045e+11 accepted 0  lowest_f -1.62778e+13
(pid=145315) basinhopping step 0: f -3.02658e+11
(pid=145315) basinhopping step 1: f -3.02658e+11 trial_f 1.28342e+07 accepted 0  lowest_f -3.02658e+11
(pid=145328) basinhopping step 2: f -1.62778e+13 trial_f 2.22501e+11 accepted 0  lowest_f -1.62778e+13
(pid=145312) basinhopping step 1: f 1.08789e+08 trial_f 1.08789e+08 accepted 1  lowest_f 1.08789e+08
(pid=145312) found new global minimum on step 1 with function value 1.08789e+08
(pid=145406) basinhopping step 0: f -1.47702e+11
(pid=145408) basinhopping step 0: f -2.68919e+11
(pid=145328) warning: basinhopping: local minimization failure
(pid=145328) basinhopping step 3: f -1.62778e+13 trial_f 3.30934e+14 accepted 0  lowest_f -1.62778e+13
(pid=145407) basinhopping step 1: f 6.2945e+07 trial_

(pid=145328) basinhopping step 7: f -1.62778e+13 trial_f 3.05516e+11 accepted 0  lowest_f -1.62778e+13
(pid=145463) basinhopping step 0: f 8.37207e+07
(pid=145312) basinhopping step 7: f 1.96479e+07 trial_f 3.69473e+09 accepted 0  lowest_f 1.96479e+07
(pid=145312) basinhopping step 8: f 1.96479e+07 trial_f 1.99204e+09 accepted 0  lowest_f 1.96479e+07
(pid=145328) basinhopping step 8: f -1.76945e+13 trial_f -1.76945e+13 accepted 1  lowest_f -1.76945e+13
(pid=145328) found new global minimum on step 8 with function value -1.76945e+13
(pid=145406) basinhopping step 6: f -1.47702e+11 trial_f 1.0911e+07 accepted 0  lowest_f -1.47702e+11
(pid=145406) basinhopping step 7: f -1.47702e+11 trial_f 8.12009e+10 accepted 0  lowest_f -1.47702e+11
(pid=145312) /home/ats4i/anaconda3/lib/python3.7/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
(pid=145312)   warnings.warn(war

(pid=145410) basinhopping step 2: f -1.47185e+11 trial_f 1.35538e+07 accepted 0  lowest_f -1.47185e+11
(pid=145463) basinhopping step 8: f -3.24304e+11 trial_f 7.9443e+07 accepted 0  lowest_f -3.24304e+11
(pid=145445) basinhopping step 5: f -1.64032e+13 trial_f 4.03516e+07 accepted 0  lowest_f -1.64032e+13
(pid=2856) basinhopping step 0: f -3.04978e+11
(pid=145453) basinhopping step 5: f -1.445e+11 trial_f -8.55159e+10 accepted 0  lowest_f -1.445e+11
(pid=145445) basinhopping step 6: f -1.64032e+13 trial_f 2.98127e+11 accepted 0  lowest_f -1.64032e+13
(pid=145453) basinhopping step 6: f -1.445e+11 trial_f 2.15708e+08 accepted 0  lowest_f -1.445e+11
(pid=145413) warning: basinhopping: local minimization failure
(pid=145413) basinhopping step 3: f -1.24484e+11 trial_f 9.0888e+07 accepted 0  lowest_f -1.24484e+11
(pid=145412) basinhopping step 3: f -1.63446e+11 trial_f 2.85943e+09 accepted 0  lowest_f -1.63446e+11
(pid=145445) basinhopping step 7: f -1.64032e+13 trial_f 7.16119e+07 accept

(pid=2856) basinhopping step 8: f -3.04978e+11 trial_f 2.43436e+10 accepted 0  lowest_f -3.04978e+11
(pid=2857) basinhopping step 9: f -1.25138e+11 trial_f 1.84699e+08 accepted 0  lowest_f -1.25138e+11
(pid=5245) basinhopping step 4: f -1.25216e+11 trial_f 1.21288e+11 accepted 0  lowest_f -1.25216e+11
(pid=6653) basinhopping step 4: f -1.25607e+11 trial_f 2.40716e+09 accepted 0  lowest_f -1.25607e+11
(pid=7331) basinhopping step 0: f -3.74611e+11
(pid=2857) basinhopping step 10: f -1.25138e+11 trial_f -1.25126e+11 accepted 0  lowest_f -1.25138e+11
(pid=6653) basinhopping step 5: f -1.25607e+11 trial_f 1.10336e+09 accepted 0  lowest_f -1.25607e+11
(pid=2856) basinhopping step 9: f -3.04978e+11 trial_f 1.72514e+08 accepted 0  lowest_f -3.04978e+11
(pid=7331) basinhopping step 1: f -3.74611e+11 trial_f 2.50645e+09 accepted 0  lowest_f -3.74611e+11
(pid=7329) basinhopping step 0: f 6.29401e+07
(pid=5245) basinhopping step 5: f -1.25216e+11 trial_f 1.84269e+08 accepted 0  lowest_f -1.25216e

(pid=10603) basinhopping step 1: f -3.65932e+11 trial_f -3.65932e+11 accepted 1  lowest_f -3.65932e+11
(pid=10603) found new global minimum on step 1 with function value -3.65932e+11
(pid=5244) basinhopping step 6: f -1.64652e+13 trial_f 3.89334e+11 accepted 0  lowest_f -1.64652e+13
(pid=10629) basinhopping step 2: f 8.37193e+07 trial_f 1.0925e+09 accepted 0  lowest_f 8.37193e+07
(pid=10629) basinhopping step 3: f 8.37193e+07 trial_f 8.37311e+07 accepted 0  lowest_f 8.37193e+07
(pid=5244) basinhopping step 7: f -1.64652e+13 trial_f 1.29194e+10 accepted 0  lowest_f -1.64652e+13
(pid=10603) basinhopping step 2: f -3.65932e+11 trial_f 1.76831e+08 accepted 0  lowest_f -3.65932e+11
(pid=8159) basinhopping step 5: f -3.07696e+11 trial_f -2.894e+10 accepted 0  lowest_f -3.07696e+11
(pid=10628) basinhopping step 3: f -2.88502e+11 trial_f -2.88502e+11 accepted 1  lowest_f -2.88502e+11
(pid=10628) found new global minimum on step 3 with function value -2.88502e+11
(pid=8158) basinhopping step 9:

...

(pid=75579) basinhopping step 1: f -1.15007e+11 trial_f 1.51723e+07 accepted 0  lowest_f -1.15007e+11
(pid=75604) basinhopping step 1: f 8.43051e+07 trial_f 2.75258e+08 accepted 0  lowest_f 8.43051e+07
(pid=75131) basinhopping step 6: f -8.09032e+13 trial_f 9.36781e+08 accepted 0  lowest_f -8.09032e+13
(pid=75578) basinhopping step 1: f -3.13724e+11 trial_f 1.82502e+08 accepted 0  lowest_f -3.13724e+11
(pid=75316) basinhopping step 7: f -1.37125e+12 trial_f 9.06594e+10 accepted 0  lowest_f -1.37125e+12
(pid=75131) basinhopping step 7: f -8.09032e+13 trial_f 2.33912e+12 accepted 0  lowest_f -8.09032e+13
(pid=75579) basinhopping step 2: f -1.15007e+11 trial_f 1.36657e+07 accepted 0  lowest_f -1.15007e+11
(pid=75131) basinhopping step 8: f -8.09032e+13 trial_f 2.39808e+10 accepted 0  lowest_f -8.09032e+13
(pid=75604) basinhopping step 2: f 3.04807e+06 trial_f 3.04807e+06 accepted 1  lowest_f 3.04807e+06
(pid=75604) found new global minimum on step 2 with function value 3.04807e+06
(pid=75

(pid=75578) basinhopping step 8: f -3.16678e+11 trial_f 3.58256e+08 accepted 0  lowest_f -3.16678e+11
(pid=75872) basinhopping step 4: f -5.25989e+11 trial_f 2.82235e+11 accepted 0  lowest_f -5.25989e+11
(pid=75578) basinhopping step 9: f -3.16678e+11 trial_f 3.70878e+08 accepted 0  lowest_f -3.16678e+11
(pid=75604) basinhopping step 9: f 3.04807e+06 trial_f 1.32402e+08 accepted 0  lowest_f 3.04807e+06
(pid=75872) basinhopping step 5: f -5.25989e+11 trial_f 1.13392e+08 accepted 0  lowest_f -5.25989e+11
(pid=75871) basinhopping step 8: f -5.51018e+11 trial_f -3.78585e+11 accepted 0  lowest_f -5.51018e+11
(pid=75578) basinhopping step 10: f -3.16678e+11 trial_f 5.88302e+10 accepted 0  lowest_f -3.16678e+11
(pid=75604) basinhopping step 10: f 3.04807e+06 trial_f 8.44035e+07 accepted 0  lowest_f 3.04807e+06
(pid=75957) basinhopping step 8: f -8.1092e+13 trial_f -3.51613e+13 accepted 0  lowest_f -8.1092e+13
(pid=75579) basinhopping step 9: f -2.77236e+11 trial_f -2.53141e+11 accepted 0  low

(pid=76684) basinhopping step 6: f -1.92092e+09 trial_f 1.49664e+08 accepted 0  lowest_f -1.92092e+09
(pid=76684) basinhopping step 7: f -1.92092e+09 trial_f 1.49664e+08 accepted 0  lowest_f -1.92092e+09
(pid=76683) basinhopping step 7: f -7.25332e+11 trial_f -2.76234e+11 accepted 0  lowest_f -7.25332e+11
(pid=76667) basinhopping step 8: f -2.88295e+11 trial_f -2.88295e+11 accepted 1  lowest_f -2.88295e+11
(pid=76667) found new global minimum on step 8 with function value -2.88295e+11
(pid=76684) warning: basinhopping: local minimization failure
(pid=76684) basinhopping step 8: f -1.92092e+09 trial_f 1.40506e+08 accepted 0  lowest_f -1.92092e+09
(pid=76683) basinhopping step 8: f -7.25332e+11 trial_f 2.83233e+11 accepted 0  lowest_f -7.25332e+11
(pid=75982) basinhopping step 6: f -5.88447e+11 trial_f 6.97973e+09 accepted 0  lowest_f -5.88447e+11
(pid=76594) basinhopping step 6: f -8.09331e+13 trial_f -8.09331e+13 accepted 1  lowest_f -8.09331e+13
(pid=76594) found new global minimum on

(pid=76931) basinhopping step 5: f -5.75569e+11 trial_f 2.80013e+11 accepted 0  lowest_f -5.75569e+11
(pid=77076) basinhopping step 4: f -8.11856e+13 trial_f 2.27302e+13 accepted 0  lowest_f -8.11856e+13
(pid=76930) basinhopping step 9: f -5.86816e+11 trial_f 7.93754e+07 accepted 0  lowest_f -5.86816e+11
(pid=77076) warning: basinhopping: local minimization failure
(pid=77076) basinhopping step 5: f -8.11856e+13 trial_f 9.42306e+08 accepted 0  lowest_f -8.11856e+13
(pid=77022) basinhopping step 3: f -4.01859e+11 trial_f 3.70665e+08 accepted 0  lowest_f -4.01859e+11
(pid=76931) basinhopping step 6: f -5.75569e+11 trial_f 2.49248e+08 accepted 0  lowest_f -5.75569e+11
(pid=77076) basinhopping step 6: f -8.11856e+13 trial_f 9.41883e+08 accepted 0  lowest_f -8.11856e+13
(pid=76931) /home/ats4i/anaconda3/lib/python3.7/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.


(pid=77077) basinhopping step 4: f -5.78063e+11 trial_f 5.53415e+10 accepted 0  lowest_f -5.78063e+11
(pid=76852) basinhopping step 9: f -6.41733e+11 trial_f 1.15499e+08 accepted 0  lowest_f -6.41733e+11
(pid=77360) warning: basinhopping: local minimization failure
(pid=77360) basinhopping step 6: f -2.59303e+13 trial_f 1.00885e+13 accepted 0  lowest_f -2.59303e+13
(pid=77335) basinhopping step 1: f -2.74683e+11 trial_f -1.26272e+11 accepted 0  lowest_f -2.74683e+11
(pid=77210) basinhopping step 2: f -2.26877e+11 trial_f 4.68448e+10 accepted 0  lowest_f -2.26877e+11
(pid=77210) basinhopping step 3: f -2.26877e+11 trial_f 1.13392e+08 accepted 0  lowest_f -2.26877e+11
(pid=77210) basinhopping step 4: f -2.26877e+11 trial_f 2.82728e+11 accepted 0  lowest_f -2.26877e+11
(pid=76852) basinhopping step 10: f -6.41733e+11 trial_f -4.36048e+11 accepted 0  lowest_f -6.41733e+11
(pid=77335) basinhopping step 2: f -2.74683e+11 trial_f 1.31975e+09 accepted 0  lowest_f -2.74683e+11
(pid=77335) basin

In [ ]:

for i in range(0,len(states)):
    state=states[i]
    query = dfparam.query('state == "{}"'.format(state)).reset_index()
    parameters = np.array(query.iloc[:, 2:])[0]
    startdate,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec = parameters
    
    Date = datetime.strptime(startdate, "%Y-%m-%d")
    end_date = Date + timedelta(days=+int(optimal[i][1]))
    dateStr=end_date.strftime("%Y-%m-%d")
    print(state[i]+" State of Brazil")
    print("S0 = {}\n".format(optimal[i][0]))
    print("Delta Date Days = {}\n".format(optimal[i][1]))   
    print("I0 = {}\n".format(optimal[i][2]))
    print("wcases = {}\n".format(optimal[i][3]))
    print("wrec = {}\n".format(optimal[i][4]))
    
    j = query['index'].values[0]
    dfparam.at[j, "s0"] = optimal[i][0]
    dfparam.at[j, "i0"] = optimal[i][2]
    dfparam.at[j, "start-date"] = dateStr
    dfparam.at[j, "WCASES"] = optimal[i][3]
    dfparam.at[j, "WREC"] = optimal[i][4]
    dfparam.to_csv("data/param_optimized_Brute_Force.csv", sep=",", index=False)
    dfparam